In [1]:
import plotly.offline as py
from plotly.subplots import make_subplots
import plotly.graph_objs as go
import plotly.express as px

import matplotlib.pyplot as plt
import smopy
%matplotlib inline

from sentiance.walk_drive import *

In [2]:
sensors_df, labels_df = load_data(
      "../data/sensors.csv",
      "../data/labels.csv"
)
  
n_segments = int(sensors_df.shape[1]/4)
n_samples = sensors_df.shape[0]

In [3]:
sample_frequency = determine_sample_frequency(sensors_df)
print(sample_frequency)

26.0


In [4]:
total_accelerations, labels = preprocess_data(
      sensors_df, 
      labels_df, 
      n_segments, 
      n_samples
)

In [5]:
fig = make_subplots(rows=22, cols=1)

for seg_id in range(n_segments):
    fig.add_trace(go.Scatter( 
            y= total_accelerations[seg_id,:],
            name="linear",
            line_shape='linear',
            line={"color":"red" if labels[seg_id]==1 else "blue"}
        ),
        row=seg_id++1, col=1
    )

fig.update_layout(height=1400, width=1000, showlegend=False)    
fig.show()

In [6]:
xF, ffts = compute_ffts(total_accelerations, sample_frequency)

In [7]:
fig = make_subplots(rows=22, cols=1)

for seg_id in range(n_segments):
    fig.add_trace(go.Scatter(
            x=xF,
            y= ffts[seg_id,1:],
            name="linear",
            line_shape='linear',
            line={"color":"red" if labels[seg_id]==1 else "blue"}
        ),
        row=seg_id++1, col=1
    )

fig.update_layout(height=1400, width=1000, showlegend=False)    
fig.show()

In [8]:
feature_matrix = compute_feature_matrix(total_accelerations, sample_frequency)

In [9]:
classifier = build_classifier(feature_matrix, labels)

In [10]:
x, y = compute_decision_boundary(classifier, feature_matrix)

In [11]:
fig = go.Figure()

fig.add_trace(
    go.Scatter(
        x=feature_matrix[labels==0,0],
        y=feature_matrix[labels==0,1],
        mode="markers"
    )
)

fig.add_trace(
    go.Scatter(
        x=feature_matrix[labels==1,0],
        y=feature_matrix[labels==1,1],
        mode="markers"
    )
)

fig.add_trace(
    go.Scatter(
        x=x,
        y=y,
        mode="lines"
    )
)

fig.update_layout(height=600, width=800, showlegend=False)    
fig.show()